Working through this http://bokeh.pydata.org/en/latest/docs/user_guide.html

In [4]:
import os
from collections import OrderedDict
from igor.binarywave import Waves
import numpy as np
from bokeh.plotting import figure
from bokeh.embed import components
from bokeh.models import Range1d, ColumnDataSource, HoverTool
from bokeh.models.mappers import LinearColorMapper

# define colormap
greys = ['#{0:02x}{0:02x}{0:02x}'.format(i) for i in range(0,256)]
viridis = ['#440154', '#440255', '#440357', '#450558', '#45065a', '#45085b', '#46095c', 
           '#460b5e', '#460c5f', '#460e61', '#470f62', '#471163', '#471265', '#471466', 
           '#471567', '#471669', '#47186a', '#48196b', '#481a6c', '#481c6e', '#481d6f', 
           '#481e70', '#482071', '#482172', '#482273', '#482374', '#472575', '#472676', 
           '#472777', '#472878', '#472a79', '#472b7a', '#472c7b', '#462d7c', '#462f7c', 
           '#46307d', '#46317e', '#45327f', '#45347f', '#453580', '#453681', '#443781', 
           '#443982', '#433a83', '#433b83', '#433c84', '#423d84', '#423e85', '#424085', 
           '#414186', '#414286', '#404387', '#404487', '#3f4587', '#3f4788', '#3e4888', 
           '#3e4989', '#3d4a89', '#3d4b89', '#3d4c89', '#3c4d8a', '#3c4e8a', '#3b508a', 
           '#3b518a', '#3a528b', '#3a538b', '#39548b', '#39558b', '#38568b', '#38578c', 
           '#37588c', '#37598c', '#365a8c', '#365b8c', '#355c8c', '#355d8c', '#345e8d', 
           '#345f8d', '#33608d', '#33618d', '#32628d', '#32638d', '#31648d', '#31658d', 
           '#31668d', '#30678d', '#30688d', '#2f698d', '#2f6a8d', '#2e6b8e', '#2e6c8e', 
           '#2e6d8e', '#2d6e8e', '#2d6f8e', '#2c708e', '#2c718e', '#2c728e', '#2b738e', 
           '#2b748e', '#2a758e', '#2a768e', '#2a778e', '#29788e', '#29798e', '#287a8e', 
           '#287a8e', '#287b8e', '#277c8e', '#277d8e', '#277e8e', '#267f8e', '#26808e', 
           '#26818e', '#25828e', '#25838d', '#24848d', '#24858d', '#24868d', '#23878d', 
           '#23888d', '#23898d', '#22898d', '#228a8d', '#228b8d', '#218c8d', '#218d8c', 
           '#218e8c', '#208f8c', '#20908c', '#20918c', '#1f928c', '#1f938b', '#1f948b', 
           '#1f958b', '#1f968b', '#1e978a', '#1e988a', '#1e998a', '#1e998a', '#1e9a89', 
           '#1e9b89', '#1e9c89', '#1e9d88', '#1e9e88', '#1e9f88', '#1ea087', '#1fa187', 
           '#1fa286', '#1fa386', '#20a485', '#20a585', '#21a685', '#21a784', '#22a784', 
           '#23a883', '#23a982', '#24aa82', '#25ab81', '#26ac81', '#27ad80', '#28ae7f', 
           '#29af7f', '#2ab07e', '#2bb17d', '#2cb17d', '#2eb27c', '#2fb37b', '#30b47a', 
           '#32b57a', '#33b679', '#35b778', '#36b877', '#38b976', '#39b976', '#3bba75', 
           '#3dbb74', '#3ebc73', '#40bd72', '#42be71', '#44be70', '#45bf6f', '#47c06e', 
           '#49c16d', '#4bc26c', '#4dc26b', '#4fc369', '#51c468', '#53c567', '#55c666', 
           '#57c665', '#59c764', '#5bc862', '#5ec961', '#60c960', '#62ca5f', '#64cb5d', 
           '#67cc5c', '#69cc5b', '#6bcd59', '#6dce58', '#70ce56', '#72cf55', '#74d054', 
           '#77d052', '#79d151', '#7cd24f', '#7ed24e', '#81d34c', '#83d34b', '#86d449', 
           '#88d547', '#8bd546', '#8dd644', '#90d643', '#92d741', '#95d73f', '#97d83e', 
           '#9ad83c', '#9dd93a', '#9fd938', '#a2da37', '#a5da35', '#a7db33', '#aadb32', 
           '#addc30', '#afdc2e', '#b2dd2c', '#b5dd2b', '#b7dd29', '#bade27', '#bdde26', 
           '#bfdf24', '#c2df22', '#c5df21', '#c7e01f', '#cae01e', '#cde01d', '#cfe11c', 
           '#d2e11b', '#d4e11a', '#d7e219', '#dae218', '#dce218', '#dfe318', '#e1e318', 
           '#e4e318', '#e7e419', '#e9e419', '#ece41a', '#eee51b', '#f1e51c', '#f3e51e', 
           '#f6e61f', '#f8e621', '#fae622', '#fde724']

def get_1d_DataSource(w):
    """ Return ColumnDataSource for 1d wave. """
    return ColumnDataSource(data=dict(x=w.x, y=w.y))
    
def get_2d_DataSource(w, cmap):
    """ return ColumnDataSource for 2d wave. """

    dmin = np.amin(w.y)
    dmax = np.amax(w.y)

    if dmin<0.0:
        idata = (w.y.flatten()-dmin)*255/(dmax-dmin)
    else:
        idata = w.y.flatten()*255/(dmax-dmin)
    cidx = idata.astype(np.uint8)
    colors = [cmap[i] for i in cidx]
    
    return ColumnDataSource(data=dict(x=w.x[:,:,0].flatten(), y=w.x[:,:,1].flatten(), 
                            data=w.y.flatten(), color=colors, cidx=cidx))

def plot_1d_wave(w, plot, hover=True):
    """ plot 1d wave as a bokeh line. """
    source = get_1d_DataSource(w)
    plot.line('x', 'y', source=source, line_width=2, line_color='firebrick')
    if hover:
        plot.add_tools(HoverTool())
        hover = plot.select(dict(type=HoverTool))
        hover.tooltips = OrderedDict([
            ('y', '@y'),
            ('x', '@x'),
        ])
    
def plot_2d_wave_rect(w, plot, cmap, hover=True):
    """ Ceates a 2d colormap by plotting many rectangles of the correct color.
        This method allows bokeh tools like HoverTool to be used to interact with
        the data. Such methods are not possible with plot.image(). """
    
    N, M = w.y.shape
    dmin = np.amin(w.y)
    dmax = np.amax(w.y)
    dw = w.extent[1]-w.extent[0]
    dh = w.extent[3]-w.extent[2]
    source = get_2d_DataSource(w, cmap)
    plot.rect('x','y', width=(dw)/(M-1), height=(dh)/(N-1), 
              color='color', line_color = 'color', source=source)
    plot.set(x_range=Range1d(w.extent[0], w.extent[1]), 
             y_range=Range1d(w.extent[2], w.extent[3]))
  
    if hover:
        plot.add_tools(HoverTool())
        hover = plot.select(dict(type=HoverTool))
        hover.tooltips = OrderedDict([
            ('value', '@data'),
        ])

def plot_2d_wave_img(w, plot, cmap):
    """ Ceates a 2d colormap by plotting many rectangles of the correct color.
        This method allows bokeh tools like HoverTool to be used to interact with
        the data. Such methods are not possible with plot.image(). """
    x = w.extent[0]
    y = w.extent[2]
    dw = w.extent[1]-w.extent[0]
    dh = w.extent[3]-w.extent[2]
    plot.image(image=[w.y], x=[x], y=[y], dw=[dw], dh=[dh], 
               color_mapper=LinearColorMapper(cmap))
    plot.set(x_range=Range1d(w.extent[0], w.extent[1]), 
             y_range=Range1d(w.extent[2], w.extent[3]))

def get_html_plot(filename):
    """ Function that will generate plots then output the html
        div and javascript elements to display that code on the webpage. """
    
    # get some file name information
    dat, ext = os.path.splitext(os.path.basename(filename))
    
    # setup figure
#     TOOLS='pan, wheel_zoom, box_zoom, resize, reset, save'
    plot = figure(plot_width=700, plot_height=500, 
                  title=dat, title_text_font_size='10pt')
    plot.logo = None
    
    # import wave dat
    try:
        w = Waves(filename, transpose=True)
    except Exception as e:
        raise ImportError('Cannot load wave from .ibw: {0}'.format(e))

    if w.d == 1:
        plot_1d_wave(w, plot, hover=False)
    elif w.d == 2: 
        plot_2d_wave_img(w, plot, viridis)
#         plot_2d_wave_rect(w, plot, viridis, hover=True)
    else:
        # add text to plot indicating that there was an error
        raise ValueError('Number of wave dimensions is greater than 2.')
        
    return plot

In [5]:
w = Waves('test_data/dat19g2d1x.ibw')

cmap = viridis

# setup figure
TOOLS='pan, wheel_zoom, box_zoom, resize, reset, save'
plot = figure(plot_width=700, plot_height=500, 
              title='test', title_text_font_size='10pt', tools=TOOLS)
plot.logo = None

N, M = w.y.shape
dmin = np.amin(w.y)
dmax = np.amax(w.y)

# create a column data source for the plots to share
if dmin<0.0:
    idata = (w.y.flatten()-dmin)*255/(dmax-dmin)
else:
    idata = w.y.flatten()*255/(dmax-dmin)
cidx = idata.astype(np.uint8)
colors = [cmap[i] for i in cidx]
source = ColumnDataSource(data=dict(x=w.x[:,:,0].flatten(), y=w.x[:,:,1].flatten(), 
                        data=w.y.flatten(), color=colors, cidx=cidx))

dmin = np.amin(w.y)
dmax = np.amax(w.y)    
source = get_2d_DataSource(w, cmap)
dw = w.extent[1]-w.extent[0]
dh = w.extent[3]-w.extent[2]
plot.rect('x','y', width=dw/(M-1), height=dh/(N-1), 
          color='color', line_color = 'color', source=source)
plot.set(x_range=Range1d(w.extent[0], w.extent[1]), y_range=Range1d(w.extent[2], w.extent[3]))

show(plot)

In [61]:
def float_to_uint8(a):
    """ Convert np.float array to np.uint8 array. """
    dmin = np.amin(a[np.isfinite(a)])
    dmax = np.amax(a[np.isfinite(a)])
    
    idata = a.flatten()
    idata[np.isnan(idata)] = dmin
    idata = (idata-dmin)*255/(dmax-dmin)
    return idata.astype(np.uint8)

In [60]:
print w.y.flatten(), float_to_uint8(w.y.flatten())

[ 0.0105591   0.00987059  0.00991255 ...,         nan         nan
         nan] [130 107 108 ...,   0   0   0]
